In [1]:
# upgrade in command line for specific interpreter

import sys
sys.executable
# /Users/lianfeng/Document/species_richness_sdm/venv/bin/pip install --upgrade tensorflow

'/Users/lianfeng/miniconda3/envs/tf/bin/python'

In [1]:
# 
exec('from __future__ import absolute_import, division, print_function, unicode_literals')

import numpy as np
import datetime
import pathlib
from sqlalchemy import create_engine
import matplotlib.pyplot as plt
import pandas as pd
import seaborn as sns
from sklearn.model_selection import train_test_split
from sklearn import preprocessing
from sklearn.preprocessing import MinMaxScaler
from sklearn.impute import KNNImputer

from tensorflow import keras
from tensorflow.keras import layers
from tensorflow.keras.layers import Dense, Activation, Dropout

In [2]:
from hyperopt import Trials, STATUS_OK, tpe
from hyperas import optim
from hyperas.distributions import choice, uniform

Using TensorFlow backend.


In [3]:
def data():
    localhost = {'user': 'postgres', 'password': 'postgres', 'host': 'localhost', 'port': 5432, 'db': 'fiadb'}
    params = 'postgresql://{0}:{1}@{2}:{3}/{4}'
    engine = create_engine(params.format(localhost['user'], localhost['password'], localhost['host'], localhost['port'], localhost['db']))
    pergrid_base = """select distinct * from predictor.pergrid_base"""
    pergrid_base_df = pd.read_sql(pergrid_base, engine)

    # separate predictor variables from outcome varaible
    y = pergrid_base_df['tsr']
    grid_id = pergrid_base_df['grid_id']
    pred_var= ['aet', 'ai', 'art', 'ewd', 'fa', 'map', 'mat', 'mpdq',
           'mtcq', 'pet', 'psn', 'ra', 'rmap', 'rmat', 'tsn', 'mfdf', 'alt','shg','mtwq','wa']
    pergrid_base_pred_df = pergrid_base_df[pred_var]

    # fill NaN with values from neighbor pixels
    imputer = KNNImputer(n_neighbors=5)
    pergrid_base_filled = imputer.fit_transform(pergrid_base_pred_df)
    pergrid_base_df = pd.DataFrame(pergrid_base_filled)
    pergrid_base_df.head()

    ss = MinMaxScaler()
    X_std = ss.fit_transform(pergrid_base_df)

    Xstd=pd.DataFrame(data=X_std[0:,0:],
                    index=pergrid_base_pred_df.index,
                    columns=pred_var)

    x_train, x_test, y_train, y_test = train_test_split(Xstd, y, test_size=0.2, random_state=12345)
    x_train, x_val, y_train, y_val = train_test_split(x_train, y_train, test_size=0.5, random_state=12345)
    x_train, x_val, x_test, y_train, y_val, y_test = x_train.to_numpy(), x_val.to_numpy(), x_test.to_numpy(), y_train.to_numpy(), y_val.to_numpy(), y_test.to_numpy()
    return x_train, x_val, x_test, y_train, y_val, y_test

In [4]:
def create_model(x_train, y_train, x_val, y_val):

    model = keras.Sequential()
    model.add(layers.Dense({{choice([256, 512, 1024])}}, input_shape=(x_train.shape[1],)))  # tune # of units
    model.add(Activation({{choice(['relu'])}}))  # tune the activation function
    model.add(Dropout({{uniform(0, 1)}}))  # tune dropout rate

    model.add(Dense({{choice([256, 512, 1024])}}))
    model.add(Activation({{choice(['relu'])}}))
    model.add(Dropout({{uniform(0, 1)}}))
    
    model.add(Dense({{choice([256, 512, 1024])}}))
    model.add(Activation({{choice(['relu'])}}))
    model.add(Dropout({{uniform(0, 1)}}))

    # tune # of layers
    if {{choice(['three', 'four'])}} == 'four':
        model.add(Dense({{choice([256, 512, 1024])}}))
        model.add(Activation({{choice(['relu'])}}))
        model.add(Dropout({{uniform(0, 1)}}))

    model.add(Dense(1))
    model.add(Activation('linear'))

    # tune the optimizer and the learning rate
    adam = keras.optimizers.Adam(lr={{choice([10 ** -4, 10 ** -3, 10 ** -2])}})
    rmsprop = keras.optimizers.RMSprop(lr={{choice([10 ** -3, 10 ** -2, 10 ** -1])}})
    sgd = keras.optimizers.SGD(lr={{choice([10 ** -3, 10 ** -2, 10 ** -1])}})

    choiceval = {{choice(['adam', 'sgd', 'rmsprop'])}}
    if choiceval == 'adam':
        optim = adam
    elif choiceval == 'rmsprop':
        optim = rmsprop
    else:
        optim = sgd

    model.compile(loss='mean_squared_error', metrics=['mean_absolute_error'], optimizer=optim) # mean_absolute_error
    result=model.fit(x_train, y_train,
              batch_size={{choice([128, 256, 512])}},
              epochs=1000,
              verbose=2,
              validation_data=(x_val, y_val))
    
    mae, mse = model.evaluate(x_val, y_val, verbose=0)
    return {'loss': mse, 'status': STATUS_OK, 'model': model}

In [5]:
best_run, best_model = optim.minimize(model=create_model,
                                      data=data,
                                      algo=tpe.suggest,
                                      max_evals=30,
                                      trials=Trials(),
                                      notebook_name='ffnn')

>>> Imports:
#coding=utf-8

try:
    import sys
except:
    pass

try:
    import numpy as np
except:
    pass

try:
    import datetime
except:
    pass

try:
    import pathlib
except:
    pass

try:
    from sqlalchemy import create_engine
except:
    pass

try:
    import matplotlib.pyplot as plt
except:
    pass

try:
    import pandas as pd
except:
    pass

try:
    import seaborn as sns
except:
    pass

try:
    from sklearn.model_selection import train_test_split
except:
    pass

try:
    from sklearn import preprocessing
except:
    pass

try:
    from sklearn.preprocessing import MinMaxScaler
except:
    pass

try:
    from sklearn.impute import KNNImputer
except:
    pass

try:
    from tensorflow import keras
except:
    pass

try:
    from tensorflow.keras import layers
except:
    pass

try:
    from tensorflow.keras.layers import Dense, Activation, Dropout
except:
    pass

try:
    from hyperopt import Trials, STATUS_OK, tpe
except:
    pass

try:
    from hyperas im

Epoch 13/1000                                         
6124/6124 - 1s - loss: 51.7774 - mean_absolute_error: 5.1091 - val_loss: 34.4610 - val_mean_absolute_error: 4.3009

Epoch 14/1000                                         
6124/6124 - 1s - loss: 53.0365 - mean_absolute_error: 5.1464 - val_loss: 57.8680 - val_mean_absolute_error: 5.3801

Epoch 15/1000                                         
6124/6124 - 1s - loss: 49.2822 - mean_absolute_error: 4.9669 - val_loss: 33.4259 - val_mean_absolute_error: 4.0653

Epoch 16/1000                                         
6124/6124 - 1s - loss: 45.7224 - mean_absolute_error: 4.8106 - val_loss: 31.0347 - val_mean_absolute_error: 3.9263

Epoch 17/1000                                         
6124/6124 - 1s - loss: 47.1308 - mean_absolute_error: 4.8303 - val_loss: 27.3770 - val_mean_absolute_error: 3.8117

Epoch 18/1000                                         
6124/6124 - 1s - loss: 46.0497 - mean_absolute_error: 4.7681 - val_loss: 37.8577 - val_mea

Epoch 61/1000                                         
6124/6124 - 1s - loss: 24.3687 - mean_absolute_error: 3.5445 - val_loss: 21.0105 - val_mean_absolute_error: 3.2573

Epoch 62/1000                                         
6124/6124 - 1s - loss: 23.7430 - mean_absolute_error: 3.5135 - val_loss: 21.2384 - val_mean_absolute_error: 3.2757

Epoch 63/1000                                         
6124/6124 - 1s - loss: 23.2639 - mean_absolute_error: 3.4813 - val_loss: 23.6140 - val_mean_absolute_error: 3.5011

Epoch 64/1000                                         
6124/6124 - 1s - loss: 23.5546 - mean_absolute_error: 3.5135 - val_loss: 22.1107 - val_mean_absolute_error: 3.3610

Epoch 65/1000                                         
6124/6124 - 1s - loss: 24.3253 - mean_absolute_error: 3.5443 - val_loss: 22.9941 - val_mean_absolute_error: 3.3894

Epoch 66/1000                                         
6124/6124 - 1s - loss: 24.1057 - mean_absolute_error: 3.5260 - val_loss: 20.6055 - val_mea

Epoch 109/1000                                        
6124/6124 - 1s - loss: 22.3317 - mean_absolute_error: 3.4054 - val_loss: 24.1501 - val_mean_absolute_error: 3.4581

Epoch 110/1000                                        
6124/6124 - 1s - loss: 22.0238 - mean_absolute_error: 3.3760 - val_loss: 21.1908 - val_mean_absolute_error: 3.2633

Epoch 111/1000                                        
6124/6124 - 1s - loss: 22.5652 - mean_absolute_error: 3.3948 - val_loss: 19.7600 - val_mean_absolute_error: 3.1399

Epoch 112/1000                                        
6124/6124 - 1s - loss: 21.3701 - mean_absolute_error: 3.3421 - val_loss: 25.1781 - val_mean_absolute_error: 3.5139

Epoch 113/1000                                        
6124/6124 - 1s - loss: 21.5994 - mean_absolute_error: 3.3557 - val_loss: 21.9829 - val_mean_absolute_error: 3.3131

Epoch 114/1000                                        
6124/6124 - 1s - loss: 22.1933 - mean_absolute_error: 3.3832 - val_loss: 21.5465 - val_mea

Epoch 157/1000                                        
6124/6124 - 1s - loss: 21.0775 - mean_absolute_error: 3.3330 - val_loss: 21.3156 - val_mean_absolute_error: 3.3140

Epoch 158/1000                                        
6124/6124 - 1s - loss: 20.5352 - mean_absolute_error: 3.2775 - val_loss: 20.2422 - val_mean_absolute_error: 3.1705

Epoch 159/1000                                        
6124/6124 - 1s - loss: 21.4888 - mean_absolute_error: 3.3387 - val_loss: 25.4907 - val_mean_absolute_error: 3.7151

Epoch 160/1000                                        
6124/6124 - 1s - loss: 20.9548 - mean_absolute_error: 3.2733 - val_loss: 21.7159 - val_mean_absolute_error: 3.3195

Epoch 161/1000                                        
6124/6124 - 1s - loss: 21.3870 - mean_absolute_error: 3.3090 - val_loss: 20.7072 - val_mean_absolute_error: 3.2024

Epoch 162/1000                                        
6124/6124 - 1s - loss: 21.0163 - mean_absolute_error: 3.3121 - val_loss: 25.7153 - val_mea

...

Epoch 653/1000                                                                    
6124/6124 - 1s - loss: 14.1768 - mean_absolute_error: 2.6684 - val_loss: 18.2863 - val_mean_absolute_error: 3.0039

Epoch 654/1000                                                                    
6124/6124 - 1s - loss: 13.8184 - mean_absolute_error: 2.6281 - val_loss: 18.3200 - val_mean_absolute_error: 2.9918

Epoch 655/1000                                                                    
6124/6124 - 1s - loss: 13.3060 - mean_absolute_error: 2.5675 - val_loss: 18.5197 - val_mean_absolute_error: 3.0047

Epoch 656/1000                                                                    
6124/6124 - 1s - loss: 13.7963 - mean_absolute_error: 2.6289 - val_loss: 18.8274 - val_mean_absolute_error: 3.0300

Epoch 657/1000                                                                    
6124/6124 - 1s - loss: 13.6826 - mean_absolute_error: 2.6028 - val_loss: 19.0020 - val_mean_absolute_error: 3.0399

Epoch

Epoch 735/1000                                                                    
6124/6124 - 1s - loss: 13.6702 - mean_absolute_error: 2.5998 - val_loss: 18.3456 - val_mean_absolute_error: 2.9930

Epoch 736/1000                                                                    
6124/6124 - 1s - loss: 13.8465 - mean_absolute_error: 2.6072 - val_loss: 18.4131 - val_mean_absolute_error: 3.0063

Epoch 737/1000                                                                    
6124/6124 - 1s - loss: 13.2274 - mean_absolute_error: 2.5707 - val_loss: 18.2937 - val_mean_absolute_error: 3.0192

Epoch 738/1000                                                                    
6124/6124 - 1s - loss: 13.0935 - mean_absolute_error: 2.5668 - val_loss: 18.7520 - val_mean_absolute_error: 3.0324

Epoch 739/1000                                                                    
6124/6124 - 1s - loss: 13.4520 - mean_absolute_error: 2.5811 - val_loss: 18.4843 - val_mean_absolute_error: 3.0018

Epoch

Epoch 817/1000                                                                    
6124/6124 - 1s - loss: 13.0957 - mean_absolute_error: 2.5472 - val_loss: 18.7812 - val_mean_absolute_error: 3.0240

Epoch 818/1000                                                                    
6124/6124 - 1s - loss: 13.0065 - mean_absolute_error: 2.5494 - val_loss: 18.4260 - val_mean_absolute_error: 3.0034

Epoch 819/1000                                                                    
6124/6124 - 1s - loss: 12.8662 - mean_absolute_error: 2.5274 - val_loss: 18.7095 - val_mean_absolute_error: 3.0427

Epoch 820/1000                                                                    
6124/6124 - 1s - loss: 13.1513 - mean_absolute_error: 2.5496 - val_loss: 18.8684 - val_mean_absolute_error: 3.0568

Epoch 821/1000                                                                    
6124/6124 - 1s - loss: 12.8658 - mean_absolute_error: 2.5143 - val_loss: 18.7092 - val_mean_absolute_error: 3.0230

Epoch

Epoch 899/1000                                                                    
6124/6124 - 1s - loss: 12.5314 - mean_absolute_error: 2.4905 - val_loss: 18.8152 - val_mean_absolute_error: 3.0211

Epoch 900/1000                                                                    
6124/6124 - 1s - loss: 12.7218 - mean_absolute_error: 2.4953 - val_loss: 18.8682 - val_mean_absolute_error: 3.0256

Epoch 901/1000                                                                    
6124/6124 - 1s - loss: 12.5183 - mean_absolute_error: 2.4771 - val_loss: 19.0056 - val_mean_absolute_error: 3.0450

Epoch 902/1000                                                                    
6124/6124 - 1s - loss: 12.6190 - mean_absolute_error: 2.5087 - val_loss: 18.5890 - val_mean_absolute_error: 3.0157

Epoch 903/1000                                                                    
6124/6124 - 1s - loss: 12.5132 - mean_absolute_error: 2.5080 - val_loss: 18.3772 - val_mean_absolute_error: 3.0003

Epoch

Epoch 981/1000                                                                    
6124/6124 - 1s - loss: 12.1033 - mean_absolute_error: 2.4594 - val_loss: 19.0185 - val_mean_absolute_error: 3.0579

Epoch 982/1000                                                                    
6124/6124 - 1s - loss: 12.2034 - mean_absolute_error: 2.4683 - val_loss: 19.3950 - val_mean_absolute_error: 3.0633

Epoch 983/1000                                                                    
6124/6124 - 1s - loss: 12.5637 - mean_absolute_error: 2.5013 - val_loss: 19.6738 - val_mean_absolute_error: 3.0842

Epoch 984/1000                                                                    
6124/6124 - 1s - loss: 12.3795 - mean_absolute_error: 2.4878 - val_loss: 19.2870 - val_mean_absolute_error: 3.0540

Epoch 985/1000                                                                    
6124/6124 - 1s - loss: 12.1353 - mean_absolute_error: 2.4614 - val_loss: 18.9930 - val_mean_absolute_error: 3.0255

Epoch

In [6]:
print(best_run)

{'Activation': 0, 'Activation_1': 0, 'Activation_2': 0, 'Activation_3': 0, 'Dense': 2, 'Dense_1': 0, 'Dense_2': 2, 'Dense_3': 0, 'Dropout': 0.4678386838070735, 'Dropout_1': 0.05014663621801924, 'Dropout_2': 0.596664158178946, 'Dropout_3': 0, 'Dropout_4': 0.5314644029412339, 'batch_size': 1, 'choiceval': 2, 'lr': 0, 'lr_1': 0, 'lr_2': 2}


In [7]:
X_train, X_val, X_test, Y_train, Y_val, Y_test = data()

In [11]:
best_model.evaluate(X_test, Y_test, verbose=0)

[18.739075834497292, 3.0473764]

In [12]:
best_model.summary()

Model: "sequential_29"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_123 (Dense)            (None, 1024)              21504     
_________________________________________________________________
activation_123 (Activation)  (None, 1024)              0         
_________________________________________________________________
dropout_94 (Dropout)         (None, 1024)              0         
_________________________________________________________________
dense_124 (Dense)            (None, 256)               262400    
_________________________________________________________________
activation_124 (Activation)  (None, 256)               0         
_________________________________________________________________
dropout_95 (Dropout)         (None, 256)               0         
_________________________________________________________________
dense_125 (Dense)            (None, 1024)            

### Evaluation Metrics

In [13]:
from sklearn.metrics import mean_absolute_error
from sklearn.metrics import r2_score

In [14]:
Y_train_pred = best_model.predict(X_train).flatten()
print('train MAE', mean_absolute_error(Y_train_pred, Y_train))
print('train r2', r2_score(Y_train, Y_train_pred))

train MAE 1.9857312446711968
train r2 0.950216161936908


In [15]:
Y_test_pred = best_model.predict(X_test).flatten()
print('test MAE', mean_absolute_error(Y_test_pred, Y_test))
print('test r2', r2_score(Y_test, Y_test_pred))

test MAE 3.0473762532218
test r2 0.8898426196077919


In [16]:
localhost = {'user': 'postgres', 'password': 'postgres', 'host': 'localhost', 'port': 5432, 'db': 'fiadb'}
params = 'postgresql://{0}:{1}@{2}:{3}/{4}'
engine = create_engine(params.format(localhost['user'], localhost['password'], localhost['host'], localhost['port'], localhost['db']))

In [17]:
ffnn_y_test = pd.DataFrame(
    {'tsr': Y_test,
     'tsr_predicted': Y_test_pred})
ffnn_y_test.to_sql(name='ffnn_y_test', con=engine, schema='predictor', if_exists='replace', index=False)

### Make TSR predictions using the full dataset

In [28]:
# Converting lat/long to cartesian
import numpy as np

def get_cartesian(lat=None,lon=None):
    lat, lon = np.deg2rad(lat), np.deg2rad(lon)
    R = 6371 # radius of the earth
    x = R * np.cos(lat) * np.cos(lon)
    y = R * np.cos(lat) * np.sin(lon)
    return x,y

In [29]:
localhost = {'user': 'postgres', 'password': 'postgres', 'host': 'localhost', 'port': 5432, 'db': 'fiadb'}
params = 'postgresql://{0}:{1}@{2}:{3}/{4}'
engine = create_engine(params.format(localhost['user'], localhost['password'], localhost['host'], localhost['port'], localhost['db']))
pergrid_base = """select distinct * from predictor.pergrid_base"""
pergrid_base_df = pd.read_sql(pergrid_base, engine)

y_true = pergrid_base_df[['tsr']]
var= ['grid_id', 'lat', 'lon', 'aet', 'ai', 'art', 'ewd', 'fa', 'map', 'mat', 'mpdq',
       'mtcq', 'pet', 'psn', 'ra', 'rmap', 'rmat', 'tsn', 'mfdf', 'alt','shg', 'mtwq', 'wa']
pred_var= ['aet', 'ai', 'art', 'ewd', 'fa', 'map', 'mat', 'mpdq',
       'mtcq', 'pet', 'psn', 'ra', 'rmap', 'rmat', 'tsn', 'mfdf', 'alt','shg', 'mtwq', 'wa']

pergrid_base_df = pergrid_base_df[var]

pergrid_base_df['x'] = 0.0
pergrid_base_df['y'] = 0.0

for i in pergrid_base_df.index:
    lat = pergrid_base_df.at[i, 'lat']
    lon = pergrid_base_df.at[i, 'lon']
    x, y = get_cartesian(lat,lon)

    pergrid_base_df.at[i, 'x'] = x
    pergrid_base_df.at[i, 'y'] = y

id_var = ['grid_id','lat','lon','x','y']
id_df = pergrid_base_df[id_var]
pergrid_base_pred_df = pergrid_base_df[pred_var]

# fill NaN with values from neighbor pixels
imputer = KNNImputer(n_neighbors=5)
pergrid_base_filled = imputer.fit_transform(pergrid_base_pred_df)
pergrid_base_filled_df = pd.DataFrame(pergrid_base_filled)

ss = MinMaxScaler()
pergrid_base_filled_scaled_df = ss.fit_transform(pergrid_base_filled_df)
pergrid_pred_df=pd.DataFrame(data=pergrid_base_filled_scaled_df[0:,0:],
                    index=pergrid_base_pred_df.index,
                    columns=pred_var)

pergrid_df = pd.concat([id_df, pergrid_pred_df], axis=1)
grid_id = pergrid_df['grid_id']
x_train_coord, x_test_coord, y_train, y_test = train_test_split(pergrid_df, y_true, test_size=0.2, random_state=12345)
x_train_coord, x_val_coord, y_train, y_val = train_test_split(x_train_coord, y_train, test_size=0.5, random_state=12345)

x_train = x_train_coord[pred_var]
x_val = x_val_coord[pred_var]
x_test = x_test_coord[pred_var]
x_train, x_val, x_test, y_train, y_val, y_test = x_train.to_numpy(), x_val.to_numpy(), x_test.to_numpy(), y_train.to_numpy(), y_val.to_numpy(), y_test.to_numpy()

In [44]:
y_train_pred = best_model.predict(x_train).flatten()
print('train MAE', mean_absolute_error(y_train_pred, y_train))
print('train r2', r2_score(y_train, y_train_pred))

train MAE 1.9857312446711968
train r2 0.950216161936908


In [49]:
y_test_pred = best_model.predict(x_test).flatten()
print('test MAE', mean_absolute_error(y_test_pred, y_test))
print('test r2', r2_score(y_test, y_test_pred))

test MAE 3.0473762532218
test r2 0.8898426196077919


###  Kriging

In [34]:
import numpy as np
import pykrige.kriging_tools as kt
from pykrige.ok import OrdinaryKriging
import matplotlib.pyplot as plt
import warnings
warnings.filterwarnings("ignore")

In [35]:
train_residual = best_model.predict(x_train).flatten() - y_train.flatten().tolist()
train_df = x_train_coord[['grid_id', 'lat', 'lon', 'x', 'y']]
train_df['residual'] = train_residual.tolist()
train_df['tsr'] = y_train.flatten().tolist()

In [38]:
test_residual = best_model.predict(x_test).flatten() - y_test.flatten().tolist()
test_df = x_test_coord[['grid_id', 'lat', 'lon', 'x', 'y']]
test_df['residual'] = test_residual.tolist()
test_df['tsr'] = y_test.flatten().tolist()
test_df['predicted_tsr'] = best_model.predict(x_test)

In [39]:
OK = OrdinaryKriging(
    x=train_df['x'], #'lon'
    y=train_df['y'], # 'lat'
    z=train_df['residual'],
    coordinates_type='euclidean', #'geographic' euclidean
    variogram_model="gaussian", # gaussian, linear
    verbose=False,
    enable_statistics=False
)

In [40]:
predict_value_list, ss = OK.execute("points", test_df['x'], test_df['y'])

In [41]:
test_df['residual_pred'] = predict_value_list

In [42]:
test_df['predicted_tsr_kriging'] = test_df['predicted_tsr'] + test_df['residual_pred']

In [43]:
print('test MAE', mean_absolute_error(test_df['predicted_tsr'], test_df['tsr']))
print('test r2', r2_score(test_df['tsr'], test_df['predicted_tsr']))

test MAE 3.0473762532218
test r2 0.8898426196077919


In [50]:
print('test MAE', mean_absolute_error(test_df['predicted_tsr_kriging'], test_df['tsr']))
print('test r2', r2_score(test_df['tsr'], test_df['predicted_tsr_kriging']))

test MAE 3.050169108040851
test r2 0.8898528487594249


### Ingest TSR predictions to PG

In [52]:
all_residual = best_model.predict(pergrid_pred_df.to_numpy()).flatten() - y_true['tsr'].tolist()
all_df = id_df
all_df['residual'] = all_residual.tolist()
all_df['tsr'] = y_true['tsr'].tolist()
all_df['predicted_tsr'] = best_model.predict(pergrid_pred_df.to_numpy())

In [53]:
residual_pred_kriging, ss = OK.execute("points", all_df['x'], all_df['y'])
all_df['residual_pred_kriging'] = residual_pred_kriging
all_df['predicted_tsr_kriging'] = all_df['predicted_tsr'] + all_df['residual_pred_kriging']

In [54]:
all_df.to_sql(name='ffnn_kriging', con=engine, schema='predictor', if_exists='replace', index=False)

In [55]:
update_geom = """
alter table predictor.ffnn_kriging add column if not exists wkb_geometry geometry(Polygon,4269);
update predictor.ffnn_kriging A SET wkb_geometry = B.wkb_geometry
FROM predictor.pergrid_base B
WHERE A.grid_id = B.grid_id
"""

In [56]:
connection = engine.connect()
connection.execute(update_geom)